In [43]:
import pandas as pd
import math
import numpy as np
import networkx as nx
import matplotlib.pyplot as plt
import pickle
from haversine import haversine, Unit
from heapq import heappop, heappush
import geopandas as gpd

# Import customized functions
from merge_bus_subway import merge_subway_bus
from compute_shortest_paths_two_layer import compute_shortest_path


In [44]:
weekday_subway_network = pickle.load(open('subway_network_weekday.pickle', 'rb'))
weekend_subway_network = pickle.load(open('subway_network_weekend.pickle', 'rb'))
weekday_bus_network = pickle.load(open('bus_network_weekday.pickle', 'rb'))
weekend_bus_network = pickle.load(open('bus_network_weekend.pickle', 'rb'))

In [45]:
geoloc_nyc = gpd.read_file('geoloc_nyc.shp')
geoloc_nyc['centroid'] = geoloc_nyc.geometry.centroid

C:\Users\baodu\AppData\Local\Temp\ipykernel_7868\3726160264.py:2: UserWarning:

Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.




In [46]:
# Doctor locations
doctors_pos={}
nyc_doctor = pd.read_csv(r'C:\Users\baodu\Dropbox\Summer_research_2024\nyc_doctor_review.csv', encoding='unicode_escape')
nyc_doctor = nyc_doctor.dropna(subset=['Latitude', 'Longitude','Site_Name'])

for index, row in nyc_doctor.iterrows():
    curr = row['count']
    if isinstance(curr, int) or (isinstance(curr, str) and curr.isnumeric()):
        doctors_pos[row['index']] = (float(row['Latitude']), float(row['Longitude']))
 
 
# Zipcode centroids position   
centroids = geoloc_nyc['centroid'].apply(lambda geom: (geom.y, geom.x)).tolist()
zipcodes = geoloc_nyc['ZCTA5'].tolist()
centroids_pos = {}
for i in range(len(zipcodes)):
    centroids_pos[zipcodes[i]] = centroids[i]

C:\Users\baodu\AppData\Local\Temp\ipykernel_7868\4165792971.py:3: DtypeWarning:

Columns (0,1,2,5,6,12,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48,49,50,51,52,53,54,55,56,57,58,59,61,63,65,67,75,76,77,78,79,80,81,82,83,84,85,86,87,88,89,90,91,92,93,94,95,96,97,98,99,100,101,102,103,104,105,106,107,108,109,110,111,112,113,114,115,116,117,118,119,120,121,122,123,124,125,126,127,128,129,130,131,132,134,137,138,139,140,141,142,143,144,145,147,149,154,155,156,157,162,163,164,165,166,168,169,170,171,172,173,174,175,176,177,182,183,190,191,192,193,194,195,196,197,198,199,200,201,202,203,204,205,206,207,208,209,210,211,212,213,214,215,216,217,218,219,220,221,222,223,224,225,226,227,228,229,230,231,232,233,234,235,236,237,238,239,240,241,242,243,244,245,246,247,248,249,250,251,252,253,254,255,256,257,258,259,260,261,262,263,264,265,266,267,268,269,270,271,272,273,274,275,276,277,278,279,280,281,282,283,284,285,286,287,288,289,290,291,

In [47]:
# get the information of all nearby stations for each zipcode centriod
def get_nearby_stops_zipcode(centroids_pos, station_info, distance_limit):
    near_stops = {}
    for zipcode, centroid_pos in centroids_pos.items():
        for id, stop_pos in station_info.items():
            distance = haversine(centroid_pos, stop_pos, unit=Unit.METERS)
            if distance < distance_limit:
                if zipcode not in near_stops.keys():
                    near_stops[(zipcode, centroid_pos)] = [(distance, id, stop_pos)]
                else:
                    near_stops[(zipcode, centroid_pos)].append((distance, id, stop_pos))
    return near_stops

# get the information of all nearby stations for each doctor
def get_nearby_stops_doctor(doctors_pos, station_info, distance_limit):
    near_stops = {}
    for id, doctor_pos in doctors_pos.items():
        for stop_id, stop_pos in station_info.items():
            distance = haversine(doctor_pos, stop_pos, unit=Unit.METERS)
            if distance < distance_limit:
                if id not in near_stops.keys():
                    near_stops[(id, doctor_pos)] = [(distance, stop_id, stop_pos)]
                else:
                    near_stops[(id, doctor_pos)].append((distance, stop_id, stop_pos))
    return near_stops

In [48]:
def compute_path_from_zipcode_to_doctor(network, zipcode_info, doctor_info, zipcode_nearby_stations, doctor_nearby_stations, time_limit, walking_speed=1.47):
    curr_best = (None, None, time_limit)
    for stop_z in zipcode_nearby_stations:
        for stop_d in doctor_nearby_stations:
            path, transit_time = compute_shortest_path(network, stop_z[1], stop_d[1])
            time_to_station =  stop_z[0] / walking_speed /60
            time_to_doctor = stop_d[0] / walking_speed / 60
            total_time = time_to_station + transit_time + time_to_doctor

            if total_time <= curr_best[2]:
                curr_best = (path, total_time)

    if curr_best[0]:
        return curr_best
    else:
        return None
            
def access_by_subway_bus(transport_network, accessible_zipcodes, accesible_doctors, time_limit, walking_speed=1.47):
    keys = list(accesible_doctors.keys())
    zipcodes_per_doctor = {key : [] for key in keys}
    
    for doctor_info, nearby_stops_d in accesible_doctors.items():
        for zipcode_info, nearby_stops_z in accessible_zipcodes.items():
            distance = haversine(zipcode_info[1], doctor_info[1], unit=Unit.METERS)
    
            if distance<1000:
                walking_time = distance/walking_speed/60
                zipcodes_per_doctor[doctor_info].append((zipcode_info[0], "walking distance", walking_time))
            else:
                res = compute_path_from_zipcode_to_doctor(transport_network, zipcode_info, doctor_info, nearby_stops_z, nearby_stops_d, time_limit)
                if res:
                    # print(doctor_info[0])
                    zipcodes_per_doctor[doctor_info].append((zipcode_info[0], res[0], res[1]))

    return zipcodes_per_doctor

# doctor_mappings = access_by_subway(weekday_subway_network, nearby_stops_zipcodes, nearby_stops_doctors, 40)
# doctor_mappings

In [49]:
G_merged = merge_subway_bus(weekday_subway_network, weekday_bus_network)
station_info = nx.get_node_attributes(G_merged, 'pos')

# reverse the order of coordinates to lat, lon
for key, val in station_info.items():
    reversed_val = val[::-1]
    station_info[key] = reversed_val


nearby_stations_centroids = get_nearby_stops_zipcode(centroids_pos, station_info, distance_limit=500)
nearby_stations_doctors = get_nearby_stops_doctor(doctors_pos, station_info, 500)

doctor_mappings = access_by_subway_bus(G_merged, nearby_stations_centroids, nearby_stations_doctors, 20)

{'subway_101': (40.889248, -73.898583), 'subway_103': (40.884667, -73.90087), 'subway_104': (40.878856, -73.904834), 'subway_106': (40.874561, -73.909831), 'subway_107': (40.869444, -73.915279), 'subway_108': (40.864621, -73.918822), 'subway_109': (40.860531, -73.925536), 'subway_110': (40.855225, -73.929412), 'subway_111': (40.849505, -73.933596), 'subway_112 A09': (40.8406375, -73.939847), 'subway_113': (40.834041, -73.94489), 'subway_114': (40.826551, -73.95036), 'subway_115': (40.822008, -73.953676), 'subway_116': (40.815581, -73.958372), 'subway_117': (40.807722, -73.96411), 'subway_118': (40.803967, -73.966847), 'subway_119': (40.799446, -73.968379), 'subway_120': (40.793919, -73.972323), 'subway_121': (40.788644, -73.976218), 'subway_122': (40.783934, -73.979917), 'subway_123': (40.778453, -73.98197), 'subway_124': (40.77344, -73.982209), 'subway_125 A24': (40.7682715, -73.9818325), 'subway_126 A25': (40.762091999999996, -73.9849165), 'subway_D16 127 R16 725 902': (40.7551288, -

In [50]:
extracted_data = []
for key, values in doctor_mappings.items():
    doctor = key[0]
    for value in values:
        zipcode = value[0]
        travel_type = value[1] if isinstance(value[1], str) else 'multiple'
        travel_time = value[2]
        extracted_data.append([doctor, zipcode, travel_type, travel_time])

# Creating a DataFrame
df = pd.DataFrame(extracted_data, columns=['Doctor', 'Zipcode', 'Travel_Type', 'Travel_Time'])

# Saving the DataFrame to a CSV file
df.to_csv('accessibility_20mins.csv', index=False)

In [52]:
import networkx as nx
import plotly.graph_objects as go
import geopandas as gpd

def draw(new_G):
    
    pos = nx.get_node_attributes(new_G, 'pos')
    name = nx.get_node_attributes(new_G, 'name')
    label = nx.get_node_attributes(new_G, 'new_node')
    
    # Prepare Plotly data for edges
    subway_edge_x = []
    subway_edge_y = []
    
    bus_edge_x = []
    bus_edge_y = []
    
    transfer_edge_x = []
    transfer_edge_y = []
            
    def add_edge_lat_lon(edge_x, edge_y, x0, x1, y0, y1):
        edge_x.append(x0)
        edge_x.append(x1)
        edge_x.append(None)
        edge_y.append(y0)
        edge_y.append(y1)
        edge_y.append(None) 
        
    for u, v, data in new_G.edges(data=True):
        x0, y0 = pos[u]
        x1, y1 = pos[v]
        if data.get('layer') == 'transfer':
            add_edge_lat_lon(transfer_edge_x, transfer_edge_y, x0, x1, y0, y1)
        
        elif 'bus' in u and v:
            add_edge_lat_lon(bus_edge_x, bus_edge_y, x0, x1, y0, y1)
            
        elif 'subway' in u and v:
            add_edge_lat_lon(subway_edge_x, subway_edge_y, x0, x1, y0, y1)
            
    
    def create_edge_trace(name, lat, lon, color):
        return go.Scattermapbox(
            name=name,
            lat=lat,
            lon=lon,
            mode='lines',
            line=dict(width=0.6, color=color),
            hoverinfo='none'
        )

    subway_edge_trace = create_edge_trace('Subway_Routes', subway_edge_y, subway_edge_x, 'Purple')
    bus_edge_trace = create_edge_trace('Bus_Routes', bus_edge_y, bus_edge_x, 'Grey')
    transfer_edge_trace = create_edge_trace('Transfer_Edge', transfer_edge_y, transfer_edge_x, 'Red')
    
    # Prepare Plotly data for nodes
    subway_node_lat = []
    subway_node_lon = []
    subway_node_text = []
    
    bus_node_lat = []
    bus_node_lon = []
    bus_node_text = []
    
    for node in new_G.nodes():
        x, y = pos[node]
        if node.startswith('subway_'):
            subway_node_lon.append(x)
            subway_node_lat.append(y)
            subway_node_text.append((name[node],node))
        elif node.startswith('bus_'):
            bus_node_lon.append(x)
            bus_node_lat.append(y)
            bus_node_text.append((name[node],node))
            
    def create_node_trace(name, lat, lon, color, text):
        return go.Scattermapbox(
            lat=lat,
            lon=lon,
            mode='markers',
            text=text,
            textposition="top center",
            hoverinfo='text',
            name=name,
            marker=dict(
                color=color,
                size=6,
                showscale=False
        )
    )

    subway_node_trace = create_node_trace('Subway Station', subway_node_lat, subway_node_lon, 'Blue', subway_node_text)
    bus_node_trace = create_node_trace('Bus Station', bus_node_lat, bus_node_lon, 'Orange', bus_node_text)
    
    
    
    # Convert GeoDataFrame to GeoJSON
    geoloc_nyc_ = geoloc_nyc[['GEO_ID', 'ZCTA5', 'NAME', 'LSAD', 'CENSUSAREA', 'geometry']]
    geojson = geoloc_nyc_.__geo_interface__

    # Create map with ZIP code boundaries and network graph
    fig = go.Figure(go.Choroplethmapbox(
        geojson=geojson,
        locations=geoloc_nyc.index,
        z=[1] * len(geoloc_nyc),
        colorscale='Blues',
        marker_opacity=0.5,
        marker_line_width=0.5,
        showscale=False)
    )

    fig.add_trace(subway_edge_trace)
    fig.add_trace(bus_edge_trace)
    fig.add_trace(transfer_edge_trace)
    
    fig.add_trace(subway_node_trace)
    fig.add_trace(bus_node_trace)

    # Prepare data for doctors and residents (centroids)
    zipcode_name = geoloc_nyc['ZCTA5'].tolist()
    centroids_x = geoloc_nyc.centroid.x.tolist()
    centroids_y = geoloc_nyc.centroid.y.tolist()
    

    # zipcodes_count = [len(zipcodes_info) for doctor_info, zipcodes_info in doctor_mappings.items()]
    # doctor_name = [doctor_info[0] for doctor_info in doctor_mappings.keys()]
    doctor_info = [(doctor_info[0], len(zipcodes_info)) for doctor_info, zipcodes_info in doctor_mappings.items()]
    long = [doctor_info[1][1] for doctor_info, zipcodes_info in doctor_mappings.items()]
    lat = [doctor_info[1][0] for doctor_info, zipcodes_info in doctor_mappings.items()]

    # Create scatter plot for doctors
    doctor_scatter = go.Scattermapbox(
        lat=lat,
        lon=long,
        mode='markers+text',
        marker=dict(color='green', size=6, showscale=False),
        name='Doctors',
        text=doctor_info,
        hoverinfo='text'
    )

    # Create scatter plot for centroids
    centroids_scatter = go.Scattermapbox(
        lat=centroids_y,
        lon=centroids_x,
        mode='markers+text',
        marker=dict(color='red', size=6, showscale=False),
        name='Residents',
        text=zipcode_name,
        hoverinfo='text'
    )

    fig.add_trace(doctor_scatter)
    fig.add_trace(centroids_scatter)

    fig.update_layout(
        mapbox=dict(
            style="carto-positron",
            zoom=10,
            center=dict(lat=40.7128, lon=-74.0060),
            pitch=0,
            bearing=0
        ),
        # dragmode=True,
        titlefont_size=16,
        showlegend=True,
        hovermode='closest',
        margin=dict(b=20, l=5, r=5, t=40),
        annotations=[dict(
            text="Network graph with ZIP code boundaries using Plotly",
            showarrow=False,
            xref="paper", yref="paper",
            x=0.005, y=-0.002
        )],
        width=1200,
        height=900
    )
    
    fig.show()

    return new_G

draw(new_G=G_merged)

[-73.898583, -73.90182988333338, None, -73.898583, -73.897062, None, -73.898583, -73.8967465, None, -73.898583, -73.89709400000001, None, -73.898583, -73.8967925, None, -73.898583, -73.89498950000001, None, -73.898583, -73.8980895, None, -73.898583, -73.900767, None, -73.90087, -73.90182988333338, None, -73.90087, -73.90214399999999, None, -73.90087, -73.897062, None, -73.90087, -73.902808, None, -73.90087, -73.8980895, None, -73.90087, -73.900767, None, -73.904834, -73.90182988333338, None, -73.904834, -73.90804274999999, None, -73.904834, -73.90214399999999, None, -73.904834, -73.90395683333332, None, -73.904834, -73.90747, None, -73.904834, -73.90482524999999, None, -73.904834, -73.902808, None, -73.904834, -73.9051695, None, -73.904834, -73.9055465, None, -73.904834, -73.900767, None, -73.909831, -73.90804274999999, None, -73.909831, -73.91235933333333, None, -73.909831, -73.90875000000001, None, -73.909831, -73.91254400000001, None, -73.909831, -73.90747, None, -73.909831, -73.911

C:\Users\baodu\AppData\Local\Temp\ipykernel_7868\443533787.py:127: UserWarning:

Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.


C:\Users\baodu\AppData\Local\Temp\ipykernel_7868\443533787.py:128: UserWarning:

Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.


